## 3. Use cases: Uniform Zarr access across formats

In this Notebook, we modify the server script from #1 in order to enable

**Kerchunk input data**. Afterwards, we will introduce and work with the `/kerchunk` API which is a leight-weight Zarr API which hosts raw chunks without server processing.

As an example, we will host a full time series of a ERA5 Dataset to show that cloudify simplifes data access on top of kerchunk:

- 1. clients see **native zarr** and are therefore relieved from the requirements
    - to have access to kerchunk tables 
    - to parse the tables, e.g. understand *parquet* files and reserve memory
    - to retrieve data from storage backends with specific software
- 2. providers can leverage server-side processing and optimize the dataset on the fly
    - adapt precision (64 to 32)
    - regrid

### Server script

**Adaptions to Notebook #1**:

- we open data through the so called *lazy reference* mapper with
    ```python
    fsspec.get_mapper(
        lazy=True,
        )
    ```
    which we pass to xarray afterwards. This only works for kerchunked input data.

**New introduced features**:

- we add a *dict* of fspec mappern to the kerchunk plugin by setting `kp.mapper_dict` 
- we convert float64 data variables to float32
- **Remapping** for the `/zarr` plugin: we remap the data to a regular grid using a linear interpolation across longitudes. For that, `unstack` and `interp` are applied lazily to all data variables for the dask-backed API

In [1]:
%%writefile xpublish_references.py

#ssl_keyfile="/work/bm0021/k204210/cloudify/workshop/key.pem"
#ssl_certfile="/work/bm0021/k204210/cloudify/workshop/cert.pem"

from cloudify.plugins.stacer import *
from cloudify.utils.daskhelper import *
from cloudify.plugins.kerchunk import *
import xarray as xr
import xpublish as xp
import asyncio
import nest_asyncio
import sys
import os
import socket   
from contextlib import closing
nest_asyncio.apply()


def unstack(ds):
    onlydimname = [a for a in ds.dims if a not in ["time", "level", "lev"]]
    if not "lat" in ds.coords:
        if not "latitude" in ds.coords:
            raise ValueError("No latitude given")
        else:
            ds = ds.rename(latitude="lat")
    if not "lon" in ds.coords:
        if not "longitude" in ds.coords:
            raise ValueError("No longitude given")
        else:
            ds = ds.rename(longitude="lon")
    if len(onlydimname) > 1:
        raise ValueError("More than one dim: " + onlydimname)
    onlydimname = onlydimname[0]
    return (
        ds.rename({onlydimname: "latlon"})
        .set_index(latlon=("lat", "lon"))
        .unstack("latlon")
    )


def interp(ds):
    global equator_lons
    return ds.interpolate_na(dim="lon", method="linear", period=360.0).reindex(
        lon=equator_lons
    )


def find_free_port_in_range(start=9000, end=9100):
    for port in range(start, end + 1):
        try:
            with closing(socket.socket(socket.AF_INET, socket.SOCK_STREAM)) as s:
                s.bind(('', port))
                s.setsockopt(socket.SOL_SOCKET, socket.SO_REUSEADDR, 1)
            return port
        except:
            continue
    raise RuntimeError("No free port found in the specified range.")
    
if __name__ == "__main__":  # This avoids infinite subprocess creation
    import dask
    zarrcluster = asyncio.get_event_loop().run_until_complete(get_dask_cluster())
    os.environ["ZARR_ADDRESS"]=zarrcluster.scheduler._address
    
    dsname=sys.argv[1]
    testvar=sys.argv[2]
    glob_inp=sys.argv[3]

    chunks = {}
    for coord in ["lon", "lat"]:
        chunk_size = os.environ.get(f"XPUBLISH_{coord.upper()}_CHUNK_SIZE", None)
        if chunk_size:
            chunks[coord] = int(chunk_size)

    chunks["time"] = 1
    
    dsdict={}
    source="reference::/"+glob_inp
    fsmap = fsspec.get_mapper(
        source,
        remote_protocol="file",
        lazy=True,
        cache_size=0
    )
    ds=xr.open_dataset(
        fsmap,
        engine="zarr",
        chunks=chunks,
        consolidated=False
    )
    kp = KerchunkPlugin()
    kp.mapper_dict = {source:fsmap}

    ds=ds[[testvar]]
    dvs = []
    l_el = False
    for dv in ds.variables:
        if "time" in dv:
            ds[dv] = ds[dv].load()
            ds[dv].encoding["dtype"] = "float64"
            ds[dv].encoding["compressor"] = None
    
    for dv in ds.data_vars:
        print(dv)
        ds[dv].encoding["dtype"] = "float32"
        template_unstack = unstack(ds[dv].isel(time=0).load())
        if not l_el:
            equator_lons = template_unstack.sel(lat=0.0, method="nearest").dropna(
                dim="lon"
            )["lon"]
            l_el = True
            latlonchunks = {a: len(template_unstack[a]) for a in template_unstack.dims}
        template_unstack = template_unstack.chunk(**latlonchunks)
        template_interp = interp(template_unstack)
        template_unstack = template_unstack.expand_dims(**{"time": ds["time"]}).chunk(
            time=1
        )
        template_interp = template_interp.expand_dims(**{"time": ds["time"]}).chunk(
            time=1
        )
        unstacked = ds[dv].map_blocks(unstack, template=template_unstack)
        interped = unstacked.map_blocks(interp, template=template_interp)
        dsv = dask.optimize(interped)[0]
        print("optimized")
        del template_unstack, template_interp
        dvs.append(dsv)
    ds = xr.combine_by_coords(dvs)
    print("combined")
    ds=ds.drop_encoding()    
    ds.encoding["source"]=source
    for dv in ds.data_vars:
        ds[dv].encoding["dtype"] = "float32"    
    dsdict[dsname]=ds
    
    collection = xp.Rest(dsdict)
    collection.register_plugin(Stac())
    collection.register_plugin(kp)
    freeport=find_free_port_in_range()
    listen_uri_fn=f"{os.environ['HOSTNAME']}_{freeport}"
    with open(listen_uri_fn, "w"):    
        collection.serve(
            host="0.0.0.0",
            port=freeport,
            #ssl_keyfile=ssl_keyfile,
            #ssl_certfile=ssl_certfile
        )

Overwriting xpublish_references.py


We run this app with an ERA5 2D-surface, analysis dataset with daily frequency. The remapping should work for all variables at once but the registration would take a while. We therefore specify only a single test variable. 

```
dsname="era5"
testvar="100u"
glob_inp="/work/bm1344/DKRZ/kerchunks_single/testera/E5_sf_an_1D.parquet"
```

by applying:

In [ ]:
%%bash --bg
source activate /work/bm0021/conda-envs/cloudify-test
python xpublish_references.py era5 100u /work/bm1344/DKRZ/kerchunks_single/testera/E5_sf_an_1D.parquet

If sth goes wrong, you can check for *cloudify* processes that you can *kill* by ID.

In [ ]:
!ps -ef | grep k204210

In [ ]:
!kill 1211291

In [2]:
import glob
server_pattern="*dkrz.de*"
cloudify_uris=[
    "http://"+':'.join(cu.split('_'))
    for cu in sorted(glob.glob(
        server_pattern
    ))
]
#use the first
cloudify_uri=cloudify_uris[0]
print(cloudify_uri)

http://l40157.lvt.dkrz.de:9000


We have to tell the python programs to do not verify ssl certificates for our purposes:

**Xarray**

Our era dataset is available via both the *zarr* API **and** the *kerchunk* API.
They are named similar:

In [3]:
dsname="era5"
zarr_url='/'.join([cloudify_uri,"datasets",dsname,"zarr"])
kerchunk_url='/'.join([cloudify_uri,"datasets",dsname,"kerchunk"])
print(kerchunk_url)

http://l40157.lvt.dkrz.de:9000/datasets/era5/kerchunk


In [4]:
import xarray as xr
ds_raw=xr.open_zarr(kerchunk_url)#
ds_processed=xr.open_zarr(zarr_url)#

In [5]:
ds_raw

<xarray.Dataset> Size: 5TB
Dimensions:  (time: 30955, cell: 542080)
Coordinates:
    lat      (cell) float64 4MB dask.array<chunksize=(542080,), meta=np.ndarray>
    lon      (cell) float64 4MB dask.array<chunksize=(542080,), meta=np.ndarray>
  * time     (time) datetime64[ns] 248kB 1940-01-01T11:30:00 ... 2024-09-30T1...
Dimensions without coordinates: cell
Data variables: (12/40)
    100u     (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    100v     (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    10u      (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    10v      (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    2d       (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    2t       (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    ...       ...
    swvl4    (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    tcc      (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    tco3     (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    tcw      (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    tcwv     (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
    tsn      (time, cell) float64 134GB dask.array<chunksize=(1, 542080), meta=np.ndarray>
Attributes: (12/22)
    project:              ECMWF Re-Analysis
    project_id:           ERA
    institution_id:       ECMWF-DKRZ
    institution:          Data from European Centre for Medium-Range Weather ...
    source_id:            IFS
    source:               ECMWF Integrated Forecast System (IFS) CY41R2
    ...                   ...
    format:               kerchunk
    product:              reanalysis
    responsible_persons:  Angelika Heil, Fabian Wachsmann
    title:                The DKRZ ERA5 data pool. Generated using Copernicus...
    license:              The ERA5 data are published with the Copernicus Pro...
    references:           Hersbach, H., Bell, B., Berrisford, P., Hirahara, S...

In [6]:
ds_processed

<xarray.Dataset> Size: 101GB
Dimensions:  (time: 30955, lat: 640, lon: 1280)
Coordinates:
  * lat      (lat) float64 5kB -89.78 -89.51 -89.23 -88.95 ... 89.23 89.51 89.78
  * lon      (lon) float64 10kB 0.0 0.2812 0.5625 0.8438 ... 359.2 359.4 359.7
  * time     (time) datetime64[ns] 248kB 1940-01-01T11:30:00 ... 2024-09-30T1...
Data variables:
    100u     (time, lat, lon) float32 101GB dask.array<chunksize=(1, 640, 1280), meta=np.ndarray>

As expected, `ds_processed` appears on a regular grid while not yet computed. Each and every chunk is only calculated on request (`load()` or `compute()`). The data on the regular grid can be easily computed.

In [7]:
ds_raw.isel(time=-1).load()

<xarray.Dataset> Size: 182MB
Dimensions:  (cell: 542080)
Coordinates:
    lat      (cell) float64 4MB 89.78 89.78 89.78 89.78 ... -89.78 -89.78 -89.78
    lon      (cell) float64 4MB 0.0 20.0 40.0 60.0 ... 280.0 300.0 320.0 340.0
    time     datetime64[ns] 8B 2024-09-30T11:30:00
Dimensions without coordinates: cell
Data variables: (12/40)
    100u     (cell) float64 4MB 5.838 2.636 -0.8782 ... -8.296 -6.063 -2.922
    100v     (cell) float64 4MB -8.215 -9.827 -10.22 ... -6.401 -8.995 -10.81
    10u      (cell) float64 4MB 4.36 2.381 0.09148 ... -5.739 -4.711 -3.002
    10v      (cell) float64 4MB -4.953 -6.245 -6.762 ... -3.089 -4.959 -6.483
    2d       (cell) float64 4MB 259.5 259.7 259.9 260.1 ... 219.4 219.4 219.4
    2t       (cell) float64 4MB 261.9 262.1 262.3 262.5 ... 223.3 223.4 223.5
    ...       ...
    swvl4    (cell) float64 4MB 0.0 0.0 0.0 0.0 ... 0.1602 0.1602 0.1602 0.1602
    tcc      (cell) float64 4MB 0.9721 0.9683 0.9667 ... 0.9813 0.9838 0.9871
    tco3     (cell) float64 4MB 0.006883 0.006877 0.006873 ... 0.002953 0.002952
    tcw      (cell) float64 4MB 5.733 5.772 5.815 5.877 ... 0.4126 0.4126 0.4126
    tcwv     (cell) float64 4MB 5.655 5.692 5.733 5.793 ... 0.3989 0.4008 0.4008
    tsn      (cell) float64 4MB 261.7 261.9 262.1 262.4 ... 221.2 221.3 221.3
Attributes: (12/22)
    project:              ECMWF Re-Analysis
    project_id:           ERA
    institution_id:       ECMWF-DKRZ
    institution:          Data from European Centre for Medium-Range Weather ...
    source_id:            IFS
    source:               ECMWF Integrated Forecast System (IFS) CY41R2
    ...                   ...
    format:               kerchunk
    product:              reanalysis
    responsible_persons:  Angelika Heil, Fabian Wachsmann
    title:                The DKRZ ERA5 data pool. Generated using Copernicus...
    license:              The ERA5 data are published with the Copernicus Pro...
    references:           Hersbach, H., Bell, B., Berrisford, P., Hirahara, S...

In [8]:
computed=ds_processed.isel(time=-1).compute()
computed

<xarray.Dataset> Size: 3MB
Dimensions:  (lat: 640, lon: 1280)
Coordinates:
  * lat      (lat) float64 5kB -89.78 -89.51 -89.23 -88.95 ... 89.23 89.51 89.78
  * lon      (lon) float64 10kB 0.0 0.2812 0.5625 0.8438 ... 359.2 359.4 359.7
    time     datetime64[ns] 8B 2024-09-30T11:30:00
Data variables:
    100u     (lat, lon) float32 3MB 0.9216 0.9801 1.039 ... 5.942 5.907 5.872

In [9]:
import hvplot.xarray
ds_processed.isel(time=-1).squeeze().hvplot(coastline="50m")

:Overlay
   .Image.I     :Image   [lon,lat]   (100u)
   .Coastline.I :Feature   [Longitude,Latitude]

**Intake**

The default **method** for intake datasets is *kerchunk* i.e. the datasets are loaded through the kerchunk API per default.

In [10]:
intake_url='/'.join([cloudify_uri,"intake.yaml"])
print(intake_url)

http://l40157.lvt.dkrz.de:9000/intake.yaml


In [11]:
import intake
storage_options=dict(verify_ssl=False)
cat=intake.open_catalog(
    intake_url,
    storage_options=storage_options
)
list(cat)

['era5']

In [12]:
ds_raw=cat[dsname].to_dask()
ds_processed=cat[dsname](method="zarr").to_dask()

/work/bm0021/conda-envs/cloudify/lib/python3.11/site-packages/intake_xarray/base.py:21: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  'dims': dict(self._ds.dims),
/work/bm0021/conda-envs/cloudify/lib/python3.11/site-packages/intake_xarray/base.py:21: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  'dims': dict(self._ds.dims),
